### Processing Data from other Cloud Services, example WEkEO
See and register at: https://www.wekeo.eu/

#### Sample data set selected from catalog is: ESA SST CCI and C3S reprocessed sea surface temperature analyses

Product ID: EO:MO:DAT:SST_GLO_SST_L4_REP_OBSERVATIONS_010_024

The ESA SST CCI and C3S global Sea Surface Temperature Reprocessed product provides gap-free maps of daily average SST at 20 cm depth at 0.05deg. x 0.05deg. horizontal grid resolution, using satellite data from the (A)ATSRs, SLSTR and the AVHRR series of sensors (Merchant et al., 2019). The ESA SST CCI and C3S level 4 analyses were produced by running the Operational Sea Surface Temperature and Sea Ice Analysis (OSTIA) system (Good et al., 2020) to provide a high resolution (1/20deg. - approx. 5km grid resolution) daily analysis of the daily average sea surface temperature (SST) at 20 cm depth for the global ocean. 

In the data catalogue, select as filter Sea Surface Temperature


In [ ]:
#load required required libraries
from ctypes import *
lib1 = cdll.LoadLibrary(r'/home/jovyan/.local/lib/libGLdispatch.so.0.0.0')
lib1 = cdll.LoadLibrary(r'/home/jovyan/.local/lib/libGLX.so.0.0.0')
lib1 = cdll.LoadLibrary(r'/home/jovyan/.local/lib/libGL.so.1.7.0')

lib1 = cdll.LoadLibrary('/opt/conda/lib/libpython3.11.so.1.0')
lib1 = cdll.LoadLibrary('/opt/conda/envs/openeo/lib/libQt5Gui.so.5')
lib1 = cdll.LoadLibrary('/opt/conda/envs/openeo/lib/libQt5Sql.so.5')
lib1 = cdll.LoadLibrary('/opt/conda/envs/openeo/lib/libQt5Concurrent.so.5')

In [ ]:
!pip install h5py
!pip install h5netcdf

In [ ]:
#load libraries
import ilwis
import logging
import sys
from datetime import datetime
from pathlib import Path
import requests
import os
import h5py
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
import xarray as xr
import math

The HDA Client provides a fully compliant Python3 Client that can be used to search and download products using the Harmonized Data Access WEkEO API

In [ ]:
#install hda (WEkEO API)
!pip install hda -U

In [ ]:
#check version used
import pkg_resources; pkg_resources.get_distribution("hda").version

The HDA Client provides a fully compliant Python3 Client that can be used to search and download products using the Harmonized Data Access WEkEO API. First let's import the hda functions:

In [ ]:
from hda import Client, Configuration

Provide WEkEO HDA API access credentials required
A text file with your username and password has to be prepared, which should be available in the 'Home' folder under the name '.hdarc' (note the file is hidden).
The file has the following 3 line content, and replace username and password with your WEkEO login details:

+ url: https://wekeo-broker.apps.mercator.dpi.wekeo.eu/databroker
+ user: *USERNAME*
+ password:*PASSWORD*

From the 'Launcher' select press the icon 'Text File', add the 3 lines of content as required and store the file, rename it to 'hdarc'.

In [ ]:
#handle credentials (using user defined WEkEO username and password)
#create a text file with filename 'hdarc' in the current folder and add the 3 lines as indicated above

from pathlib import Path
print(Path.home())
!pwd
!mv hdarc .hdarc
!cp .hdarc /home/jovyan
!ls -a /home/jovyan
!mv .hdarc hdarc

#### Get the dataset metadata
We are going to download the ESA SST CCI and C3S reprocessed sea surface temperature analysesd dataset:EO:MO:DAT:SST_GLO_SST_L4_REP_OBSERVATIONS_010_024.

To create our request we can ask to the API what parameters are needed. To do so we use the metadata() function:

In [ ]:
hda_client = Client()
help(hda_client.metadata)

### Link to datasets in WEkEO:
https://www.wekeo.eu/data-status

In [ ]:
# Request metadata of a dataset
hda_client.metadata(dataset_id='EO:MO:DAT:SST_GLO_SST_L4_REP_OBSERVATIONS_010_024:C3S-GLO-SST-L4-REP-OBS-SST_202211')

#### Copy the 'API request' created in WEkEO into the code field below
Note the date range and the variable selected in the query statement below

In [ ]:
query = {
  "datasetId": "EO:MO:DAT:SST_GLO_SST_L4_REP_OBSERVATIONS_010_024:C3S-GLO-SST-L4-REP-OBS-SST_202211",
  "boundingBoxValues": [
    {
      "name": "bbox",
      "bbox": [
        23.77389632237424,
        34.21060732762593,
        61.683622890484514,
        51.86161159616145
      ]
    }
  ],
  "dateRangeSelectValues": [
    {
      "name": "time",
      "start": "2022-06-01T01:00:00.000Z",
      "end": "2022-06-04T23:59:59.999Z"
    }
  ],
  "multiStringSelectValues": [
    {
      "name": "variables",
      "value": [
        "analysed_sst"
      ]
    }
  ]
}

#### Search for the data

In [ ]:
matches = hda_client.search(query)
print(matches)

#### Download the files
First create / set the folder 

In [ ]:
folder = 'data'
os.chdir(".")
print("current dir is: %s" % (os.getcwd()))

if os.path.isdir(folder):
    print("Folder exists")
else:
    print("Folder doesn't exists")
    os.mkdir(folder)


You can run matches.download() to download all the files of your request.
Please [read the documentation](https://hda.readthedocs.io/en/latest/usage.html#advanced-client-usage) for advanced usage such as:

+ downloading first result: matches[0].download()
+ downloading last result: matches[-1].download()
+ downloading first 10 results: matches[:10].download()
+ downloading even results: matches[::2].download()

In [ ]:
#download all requested files
matches.download(folder)

#### Set working directory for further analysis

In [ ]:
work_dir = os.getcwd() + '/' + folder 
print(work_dir)
ilwis.setWorkingCatalog(work_dir)

### Import a selected dataset in NC format
In order to import the dataset use is made of xarray. See also the [xarray documentation](https://docs.xarray.dev/en/stable/user-guide/io.html)

In [ ]:
data = xr.load_dataset(work_dir +'/20220601120000-C3S-L4_GHRSST-SSTdepth-OSTIA-GLOB_ICDR2.1-v02.0-fv01.0.nc?analysed_sst', engine="h5netcdf")
data

In [ ]:
#get the data variable of interest, here 'analysed_sst'
sst = data["analysed_sst"]
sst.shape

In [ ]:
#check the content of the array
print(sst)

In [ ]:
#plot dataset
fig1 = plt.figure(figsize=(10, 8))
plt.imshow(sst[0], cmap='jet');

In [ ]:
#create flipped plot
#now plot with origin parameter - set to lower
fig2 = plt.figure(figsize=(10, 8))
plt.imshow(sst[0],origin='lower', cmap='jet');

#### Flip the numpy array
As can be seen from the figure above the array needs to be turned upside down. To display the 1st element to last element in steps of 1 in reverse order, we use the slicing option [::-1].
For more information on slicing review the [online documentation](https://www.freecodecamp.org/news/python-slicing-how-to-slice-an-array/)

In [ ]:
#flip array (upside down) or use np.flipud
sst1 = sst[::-1, ::-1].values
sst1.shape

In [ ]:
print(sst1)

#### Create a 1D array

In [ ]:
print('array size =',3600*7200)
sst2 = np.array([sst1]).flatten()
print(sst2.shape)
print(sst2)

#### Create the georeference and empty ilwis raster
Georeference using lat-lon (epsg:4326), specify the map dimensions, number of rows and columns and assign the coordinates to the corner of the pixel
Subsequently create the empty raster, specifying the data type (float), the initial data range to be expected, the number of columns and row and assigne the data tyoe and georeference to the empty raster map

In [ ]:
# envelope =  min X, max Y, max X, min Y,  here -180 90 180 -90 (units - degree)
# gridsize =  no columns, no rows
grf_LL= ilwis.GeoReference('code=georef:type=corners, csy=epsg:4326, envelope=-180 90 180 -90 , gridsize=7200 3600, cornerofcorners=yes')

In [ ]:
dfNum = ilwis.DataDefinition(ilwis.NumericDomain('code=value'), ilwis.NumericRange(100.0, 400.0, 0))
rcNew = ilwis.RasterCoverage()
rcNew.setSize(ilwis.Size(7200, 3600,1))
rcNew.setGeoReference(grf_LL)
rcNew.setDataDef(dfNum)

#### Read numpy array and create an ILWIS raster map

In [ ]:
rcNew.array2raster(sst2)
print(rcNew.size())

#### Convert from Kelvin to Celsius and  set data range with 2 decimals

In [ ]:
sstC = ilwis.do('mapcalc','@1-273.15',rcNew)
sstC = ilwis.do('setvaluerange', sstC, -50, 50, 0.01)
sstC.store('sst.mpr')

#### Download and display the image using ILWIS386

### Import / processing data using looping routine
Given your request multiple files have been downloaded. The example provided below shows how to import the sea surface temperature layer from multiple files and create a map stack in ILWIS and Geotif format. First we create a list of all files using the (generic) filename extension

In [ ]:
# return a list of file names
sst_list = []
# Iterate directory
for file in os.listdir(work_dir):
    # check only downloaded sst files
    if file.endswith('.nc?analysed_sst'):
        sst_list.append(work_dir +'/'+file)
print(sst_list)

#### Using a loop to import the data
xarray's engine 'h5netcdf' reads the files which are subsequently appended to the newly created list 'mdata', the file content (like dimensions, variables and attributes) is subsequently printed

In [ ]:
mdata = []
for i in sst_list:
    data = xr.open_dataset(i, engine="h5netcdf")
    mdata.append(data)
    
mdata

Read the variable 'analysed_sst' for the multiple layers and create a list with items containing the data (for each of the time steps)

In [ ]:
sstm = [multi_sst["analysed_sst"].values.flatten() for multi_sst in mdata ]
len(sstm)

Read the items of the list as a 2-D array, in the form of Z(time) and XY(sst) and return the shape

In [ ]:
sstma = np.array(sstm)
sstma.shape

Transform the array into a 3D array, using number of time steps, columns and rows (provided by the meta data) and check the (3D) shape

In [ ]:
sst_stack = sstma.reshape(len(sstm),3600, 7200)
sst_stack.shape

We now continue the processing as done for the single time step data processing, like inverting the array, defining the empty (3 dimensional) raster, assigning the previously created GeorReference and reading the NP array data

In [ ]:
sst_stackf = sst_stack[::-1, ::-1]
sst_stackf.shape

Flatten your array to 1D

In [ ]:
sstm_fin = sst_stackf.flatten()
print(sstm_fin.shape)
print(sstm_fin)

Use is made of the shape information to create the ilwis raster size dimensions, this makes the code more generic, for example if we are importing a larger time series 

In [ ]:
dfNum = ilwis.DataDefinition(ilwis.NumericDomain('code=value'), ilwis.NumericRange(100.0, 400.0, 0))
rcNew = ilwis.RasterCoverage()
rcNew.setSize(ilwis.Size(sst_stackf.shape[1],sst_stackf.shape[2],sst_stackf.shape[0]))
rcNew.setGeoReference(grf_LL)
rcNew.setDataDef(dfNum)

In [ ]:
rcNew.array2raster(sstm_fin)
print(rcNew.size())

Calculations and operations are now performed on all layers within the multi dimensional raster data stack

In [ ]:
multi_sstC = ilwis.do('mapcalc','@1-273.15',rcNew)
multi_sstC = ilwis.do('setvaluerange', multi_sstC, -50, 50, 0.01)

Store your results as ilwis maplist or geotif

In [ ]:
#ilwis format
multi_sstC.store('sst_ts.mpl')

In [ ]:
#uncomment lines below to store the result in geotif format - assigning 0 to -999
#multi_sstCT = ilwis.do('mapcalc','iff(@1==0.00000,-999,@1)',multi_sstC)
#multi_sstCT.store('sst_ts.tif', 'GTiff', 'gdal')